In [40]:
import binance
import pandas as pd
from ipywidgets import widgets
import seaborn as sns
import datetime
from matplotlib import pyplot as plt
import time
import datetime
import os
import requests
# timestamp (in ms) to start from: Dec 15th 2018
start_point = '1544844000000'

# current time: Apr 25th 11:34 am
current_point = 1556184840000

# values to ignore in your balance
low_limit = .0001 

# reference exchange for BTC valuation
btcusd = 'BTCUSDT'

# depth of history for min, hrs, day, month
depth_min = '1000'
depth_hrs = '120'
depth_day = '60'
depth_mth = '5'

keys = pd.read_csv("binancekey.csv")
api_key = keys.loc[0,"api_key"]
api_secret = keys.loc[0,"api_secret"]
binance.set(api_key, api_secret)


### fonctions réutilisables

# build function that converts time stamp to standard date/time
def clean_date(histo, value):
    histo["closeTime"] = histo["closeTime"].apply(lambda x: datetime.datetime.fromtimestamp(x/1000))
    histo["openTime"] = histo["openTime"].apply(lambda x: datetime.datetime.fromtimestamp(x/1000))
    histo["xch"] = value
    return histo

# build function that collects history by minutes/day/hours/month. 
def build_histo(minutes, hours, days, months):
    Hminutes = clean_date(pd.DataFrame(binance.klines(btcusd,minutes,limit = depth_min)),btcusd)
    Hhours = clean_date(pd.DataFrame(binance.klines(btcusd,hours,limit = depth_hrs)), btcusd)
    Hdays = clean_date(pd.DataFrame(binance.klines(btcusd,days,limit = depth_day)), btcusd)
    Hmonths = clean_date(pd.DataFrame(binance.klines(btcusd,months,limit = depth_mth)), btcusd)
    return Hminutes, Hhours, Hdays, Hmonths

In [18]:
# collect Balances
bal = pd.DataFrame(binance.balances()).transpose()["free"].astype(float)
bal = bal[bal > low_limit]

# collect current prices
price = pd.Series(binance.prices())

# build a short history wiht various aggregations:
Hminutes, Hhours, Hdays, Hmonths = build_histo('1m', '1h', '1d', '1M')


In [ ]:
# build "minutes" history of klines, and export to files
stop = False
counter = 0
limit_cycles = 100

#initialize:
temp = binance.klines(btcusd,'1m',limit = depth_min,startTime = start_point)
restart = pd.DataFrame(temp)["closeTime"].astype(int).max() + 1
result = temp
temp = []

while stop == False and restart < current_point:
    try: 
        temp = binance.klines(btcusd,'1m',limit = depth_min, startTime = restart)
        restart = pd.DataFrame(temp)["closeTime"].astype(int).max() + 1
        result.extend(temp)
        temp = []
        counter += 1
        print("done {} cycles, {} records, up to {}".format(counter, len(result), datetime.datetime.fromtimestamp(int(restart) /1000)))
        
        if counter == limit_cycles:
            filename = "data binance/archives stocks/Klines_BTC_USD_" + str(limit_cycles) + ".csv"
            pd.DataFrame(result).to_csv(filename)
            limit_cycles += 100
            result = []
        else:   
            time.sleep(1)
    except:
        stop = True
        print("Unexpected error:", sys.exc_info()[0])
        raise

filename = "data binance/archives stocks/Klines_BTC_USD_" + str(limit_cycles) + ".csv"
pd.DataFrame(result).to_csv(filename)        
print("job finished :)")        


In [76]:
# build trade history from "trades"

stop = False
counter = 0
limit_cycles = 100

#initialize:
temp = requests.get("http://www.binance.com/api/v1/aggTrades", params ={"symbol":btcusd,"startTime" : start_point, "endTime" : int(start_point)+3500000} ,headers={"X-MBX-APIKEY":api_key})

restart = pd.DataFrame(temp.json())["a"].astype(int).max() + 1
result = temp.json()
temp = []

while stop == False and restart < current_point:
    try: 
        temp = requests.get("http://www.binance.com/api/v1/aggTrades", params ={"symbol":btcusd, "fromId" : restart} ,headers={"X-MBX-APIKEY":api_key})
        restart = pd.DataFrame(temp.json())["a"].astype(int).max() + 1
        progress = pd.DataFrame(temp.json())["T"].astype(int).max() + 1
        result.extend(temp.json())
        temp = []
        counter += 1
        print("done {} cycles, {} records, up to {}".format(counter, len(result), datetime.datetime.fromtimestamp(int(progress) /1000)))
        
        if counter == limit_cycles:
            filename = "data binance/archives trades/Trades_BTCUSD_" + str(limit_cycles) + ".csv"
            pd.DataFrame(result).to_csv(filename)
            limit_cycles += 100
            result = []
        else:   
            time.sleep(1)
    except:
        stop = True
        print("Unexpected error:", sys.exc_info()[0])
        raise

filename = "data binance/archives trades/Trades_BTCUSD_" + str(limit_cycles) + ".csv"
pd.DataFrame(result).to_csv(filename)        
print("job finished :)")     

done 1 cycles, 5554 records, up to 2018-12-15 05:23:49.115000
done 2 cycles, 6054 records, up to 2018-12-15 05:30:42.035000
done 3 cycles, 6554 records, up to 2018-12-15 05:36:14.682000
done 4 cycles, 7054 records, up to 2018-12-15 05:44:04.856000
done 5 cycles, 7554 records, up to 2018-12-15 05:50:04.737000
done 6 cycles, 8054 records, up to 2018-12-15 05:58:12.489000
done 7 cycles, 8554 records, up to 2018-12-15 06:06:42.916000
done 8 cycles, 9054 records, up to 2018-12-15 06:12:40.868000
done 9 cycles, 9554 records, up to 2018-12-15 06:19:16.966000
done 10 cycles, 10054 records, up to 2018-12-15 06:25:28.960000
done 11 cycles, 10554 records, up to 2018-12-15 06:33:01.314000
done 12 cycles, 11054 records, up to 2018-12-15 06:38:25.794000
done 13 cycles, 11554 records, up to 2018-12-15 06:45:03.858000
done 14 cycles, 12054 records, up to 2018-12-15 06:47:54.847000
done 15 cycles, 12554 records, up to 2018-12-15 06:56:11.164000
done 16 cycles, 13054 records, up to 2018-12-15 07:05:35.1

done 130 cycles, 15000 records, up to 2018-12-15 16:30:20.424000
done 131 cycles, 15500 records, up to 2018-12-15 16:34:20.104000
done 132 cycles, 16000 records, up to 2018-12-15 16:40:26.500000
done 133 cycles, 16500 records, up to 2018-12-15 16:45:16.523000
done 134 cycles, 17000 records, up to 2018-12-15 16:48:43.223000
done 135 cycles, 17500 records, up to 2018-12-15 16:51:41.462000
done 136 cycles, 18000 records, up to 2018-12-15 16:55:02.014000
done 137 cycles, 18500 records, up to 2018-12-15 16:58:33.572000
done 138 cycles, 19000 records, up to 2018-12-15 17:02:13.145000
done 139 cycles, 19500 records, up to 2018-12-15 17:04:58.319000
done 140 cycles, 20000 records, up to 2018-12-15 17:07:06.188000
done 141 cycles, 20500 records, up to 2018-12-15 17:12:23.554000
done 142 cycles, 21000 records, up to 2018-12-15 17:18:38.723000
done 143 cycles, 21500 records, up to 2018-12-15 17:23:07.533000
done 144 cycles, 22000 records, up to 2018-12-15 17:30:04.009000
done 145 cycles, 22500 re

done 257 cycles, 28500 records, up to 2018-12-16 03:30:37.703000
done 258 cycles, 29000 records, up to 2018-12-16 03:32:45.353000
done 259 cycles, 29500 records, up to 2018-12-16 03:34:49.942000
done 260 cycles, 30000 records, up to 2018-12-16 03:37:29.091000
done 261 cycles, 30500 records, up to 2018-12-16 03:40:04.027000
done 262 cycles, 31000 records, up to 2018-12-16 03:44:40.820000
done 263 cycles, 31500 records, up to 2018-12-16 03:49:43.927000
done 264 cycles, 32000 records, up to 2018-12-16 03:53:44.567000
done 265 cycles, 32500 records, up to 2018-12-16 03:58:17.063000
done 266 cycles, 33000 records, up to 2018-12-16 04:03:19.512000
done 267 cycles, 33500 records, up to 2018-12-16 04:06:53.954000
done 268 cycles, 34000 records, up to 2018-12-16 04:10:19.502000
done 269 cycles, 34500 records, up to 2018-12-16 04:12:38.218000
done 270 cycles, 35000 records, up to 2018-12-16 04:15:40.259000
done 271 cycles, 35500 records, up to 2018-12-16 04:20:18.725000
done 272 cycles, 36000 re

done 384 cycles, 42000 records, up to 2018-12-16 15:48:06.384000
done 385 cycles, 42500 records, up to 2018-12-16 15:54:52.883000
done 386 cycles, 43000 records, up to 2018-12-16 16:03:45.548000
done 387 cycles, 43500 records, up to 2018-12-16 16:10:39.240000
done 388 cycles, 44000 records, up to 2018-12-16 16:17:14.441000
done 389 cycles, 44500 records, up to 2018-12-16 16:23:08.277000
done 390 cycles, 45000 records, up to 2018-12-16 16:29:55.832000
done 391 cycles, 45500 records, up to 2018-12-16 16:35:17.733000
done 392 cycles, 46000 records, up to 2018-12-16 16:43:14.763000
done 393 cycles, 46500 records, up to 2018-12-16 16:50:56.472000
done 394 cycles, 47000 records, up to 2018-12-16 16:58:36.977000
done 395 cycles, 47500 records, up to 2018-12-16 17:04:36.809000
done 396 cycles, 48000 records, up to 2018-12-16 17:12:43.916000
done 397 cycles, 48500 records, up to 2018-12-16 17:18:28.587000
done 398 cycles, 49000 records, up to 2018-12-16 17:24:53.147000
done 399 cycles, 49500 re

done 511 cycles, 5500 records, up to 2018-12-17 07:53:07.238000
done 512 cycles, 6000 records, up to 2018-12-17 08:00:15.782000
done 513 cycles, 6500 records, up to 2018-12-17 08:10:26.460000
done 514 cycles, 7000 records, up to 2018-12-17 08:18:44.209000
done 515 cycles, 7500 records, up to 2018-12-17 08:27:33.155000
done 516 cycles, 8000 records, up to 2018-12-17 08:30:01.439000
done 517 cycles, 8500 records, up to 2018-12-17 08:36:03.409000
done 518 cycles, 9000 records, up to 2018-12-17 08:41:12.579000
done 519 cycles, 9500 records, up to 2018-12-17 08:47:34.419000
done 520 cycles, 10000 records, up to 2018-12-17 08:51:00.369000
done 521 cycles, 10500 records, up to 2018-12-17 08:52:17.565000
done 522 cycles, 11000 records, up to 2018-12-17 08:55:45.073000
done 523 cycles, 11500 records, up to 2018-12-17 09:00:25.392000
done 524 cycles, 12000 records, up to 2018-12-17 09:01:38.313000
done 525 cycles, 12500 records, up to 2018-12-17 09:04:12.505000
done 526 cycles, 13000 records, up

...

done 63648 cycles, 24000 records, up to 2019-05-12 09:44:00.045000
done 63649 cycles, 24500 records, up to 2019-05-12 09:45:04.881000
done 63650 cycles, 25000 records, up to 2019-05-12 09:46:44.419000
done 63651 cycles, 25500 records, up to 2019-05-12 09:48:02.279000
done 63652 cycles, 26000 records, up to 2019-05-12 09:49:29.104000
done 63653 cycles, 26500 records, up to 2019-05-12 09:51:23.163000
done 63654 cycles, 27000 records, up to 2019-05-12 09:52:40.410000
done 63655 cycles, 27500 records, up to 2019-05-12 09:53:39.309000
done 63656 cycles, 28000 records, up to 2019-05-12 09:55:42.823000
done 63657 cycles, 28500 records, up to 2019-05-12 09:57:39.265000
done 63658 cycles, 29000 records, up to 2019-05-12 09:59:30.879000
done 63659 cycles, 29500 records, up to 2019-05-12 10:01:00.341000
done 63660 cycles, 30000 records, up to 2019-05-12 10:02:06.603000
done 63661 cycles, 30500 records, up to 2019-05-12 10:03:17.771000
done 63662 cycles, 31000 records, up to 2019-05-12 10:04:07.90

done 63771 cycles, 35500 records, up to 2019-05-12 11:29:09.394000
done 63772 cycles, 36000 records, up to 2019-05-12 11:29:37.513000
done 63773 cycles, 36500 records, up to 2019-05-12 11:30:24.674000
done 63774 cycles, 37000 records, up to 2019-05-12 11:31:33.758000
done 63775 cycles, 37500 records, up to 2019-05-12 11:32:44.435000
done 63776 cycles, 38000 records, up to 2019-05-12 11:33:44.209000
done 63777 cycles, 38500 records, up to 2019-05-12 11:35:11.019000
done 63778 cycles, 39000 records, up to 2019-05-12 11:36:29.236000
done 63779 cycles, 39500 records, up to 2019-05-12 11:36:55.920000
done 63780 cycles, 40000 records, up to 2019-05-12 11:38:08.331000
done 63781 cycles, 40500 records, up to 2019-05-12 11:39:22.339000
done 63782 cycles, 41000 records, up to 2019-05-12 11:40:40.635000
done 63783 cycles, 41500 records, up to 2019-05-12 11:42:08.470000
done 63784 cycles, 42000 records, up to 2019-05-12 11:42:41.707000
done 63785 cycles, 42500 records, up to 2019-05-12 11:42:55.50

done 63894 cycles, 47000 records, up to 2019-05-12 13:18:12.551000
done 63895 cycles, 47500 records, up to 2019-05-12 13:19:18.062000
done 63896 cycles, 48000 records, up to 2019-05-12 13:20:45.760000
done 63897 cycles, 48500 records, up to 2019-05-12 13:21:51.187000
done 63898 cycles, 49000 records, up to 2019-05-12 13:23:05.394000
done 63899 cycles, 49500 records, up to 2019-05-12 13:24:43.395000
done 63900 cycles, 50000 records, up to 2019-05-12 13:25:23.729000
done 63901 cycles, 500 records, up to 2019-05-12 13:25:55.061000
done 63902 cycles, 1000 records, up to 2019-05-12 13:26:42.796000
done 63903 cycles, 1500 records, up to 2019-05-12 13:27:05.759000
done 63904 cycles, 2000 records, up to 2019-05-12 13:27:27.897000
done 63905 cycles, 2500 records, up to 2019-05-12 13:28:04.739000
done 63906 cycles, 3000 records, up to 2019-05-12 13:28:52.168000
done 63907 cycles, 3500 records, up to 2019-05-12 13:29:35.887000
done 63908 cycles, 4000 records, up to 2019-05-12 13:30:14.289000
done

done 64017 cycles, 8500 records, up to 2019-05-12 15:06:31.459000
done 64018 cycles, 9000 records, up to 2019-05-12 15:07:43.434000
done 64019 cycles, 9500 records, up to 2019-05-12 15:08:23.801000
done 64020 cycles, 10000 records, up to 2019-05-12 15:09:20.350000
done 64021 cycles, 10500 records, up to 2019-05-12 15:10:35.154000
done 64022 cycles, 11000 records, up to 2019-05-12 15:11:34.462000
done 64023 cycles, 11500 records, up to 2019-05-12 15:12:17.481000
done 64024 cycles, 12000 records, up to 2019-05-12 15:13:12.566000
done 64025 cycles, 12500 records, up to 2019-05-12 15:14:38.069000
done 64026 cycles, 13000 records, up to 2019-05-12 15:15:33.111000
done 64027 cycles, 13500 records, up to 2019-05-12 15:17:14.360000
done 64028 cycles, 14000 records, up to 2019-05-12 15:18:23.963000
done 64029 cycles, 14500 records, up to 2019-05-12 15:19:41.023000
done 64030 cycles, 15000 records, up to 2019-05-12 15:20:33.492000
done 64031 cycles, 15500 records, up to 2019-05-12 15:21:15.47600

NameError: name 'sys' is not defined

In [72]:
test.sort_values('a')

M              T         a         f         l      m        p  \
0      True  1544844000187  77914886  86713059  86713059   True  3250.27   
10108  True  1544844000187  77914886  86713059  86713059   True  3250.27   
5054   True  1544844000187  77914886  86713059  86713059   True  3250.27   
15162  True  1544844000187  77914886  86713059  86713059   True  3250.27   
15163  True  1544844000998  77914887  86713060  86713060   True  3250.28   
10109  True  1544844000998  77914887  86713060  86713060   True  3250.28   
1      True  1544844000998  77914887  86713060  86713060   True  3250.28   
5055   True  1544844000998  77914887  86713060  86713060   True  3250.28   
15164  True  1544844001155  77914888  86713061  86713061   True  3250.28   
10110  True  1544844001155  77914888  86713061  86713061   True  3250.28   
2      True  1544844001155  77914888  86713061  86713061   True  3250.28   
5056   True  1544844001155  77914888  86713061  86713061   True  3250.28   
3      True  1544844002074  77914889  86713062  86713062   True  3250.30   
15165  True  1544844002074  77914889  86713062  86713062   True  3250.30   
5057   True  1544844002074  77914889  86713062  86713062   True  3250.30   
10111  True  1544844002074  77914889  86713062  86713062   True  3250.30   
4      True  1544844002507  77914890  86713063  86713063   True  3250.30   
15166  True  1544844002507  77914890  86713063  86713063   True  3250.30   
5058   True  1544844002507  77914890  86713063  86713063   True  3250.30   
10112  True  1544844002507  77914890  86713063  86713063   True  3250.30   
15167  True  1544844002507  77914891  86713064  86713064   True  3250.28   
5059   True  1544844002507  77914891  86713064  86713064   True  3250.28   
5      True  1544844002507  77914891  86713064  86713064   True  3250.28   
10113  True  1544844002507  77914891  86713064  86713064   True  3250.28   
5060   True  1544844002815  77914892  86713065  86713065  False  3250.68   
10114  True  1544844002815  77914892  86713065  86713065  False  3250.68   
6      True  1544844002815  77914892  86713065  86713065  False  3250.68   
15168  True  1544844002815  77914892  86713065  86713065  False  3250.68   
10115  True  1544844006778  77914893  86713066  86713066   True  3250.60   
7      True  1544844006778  77914893  86713066  86713066   True  3250.60   
...     ...            ...       ...       ...       ...    ...      ...   
15154  True  1544847496748  77919932  86718277  86718277  False  3251.20   
10100  True  1544847496748  77919932  86718277  86718277  False  3251.20   
15155  True  1544847496955  77919933  86718278  86718278  False  3251.20   
5047   True  1544847496955  77919933  86718278  86718278  False  3251.20   
20209  True  1544847496955  77919933  86718278  86718278  False  3251.20   
10101  True  1544847496955  77919933  86718278  86718278  False  3251.20   
10102  True  1544847497339  77919934  86718279  86718279  False  3251.20   
20210  True  1544847497339  77919934  86718279  86718279  False  3251.20   
15156  True  1544847497339  77919934  86718279  86718279  False  3251.20   
5048   True  1544847497339  77919934  86718279  86718279  False  3251.20   
20211  True  1544847497351  77919935  86718280  86718280  False  3251.20   
15157  True  1544847497351  77919935  86718280  86718280  False  3251.20   
10103  True  1544847497351  77919935  86718280  86718280  False  3251.20   
5049   True  1544847497351  77919935  86718280  86718280  False  3251.20   
15158  True  1544847497351  77919936  86718281  86718281  False  3251.22   
10104  True  1544847497351  77919936  86718281  86718281  False  3251.22   
5050   True  1544847497351  77919936  86718281  86718281  False  3251.22   
20212  True  1544847497351  77919936  86718281  86718281  False  3251.22   
15159  True  1544847497667  77919937  86718282  86718282  False  3251.14   
20213  True  1544847497667  77919937  86718282  86718282  False  3251.14   
5051   True  1544847497667  77919937  86718282  86718282  